Tutorial pekan ke-3, pemodelan vektor kata dan dokumen dengan Tf-Idf

Sumber: https://stackabuse.com/python-for-nlp-creating-tf-idf-model-from-scratch/ 

Import library yang dibutuhkan

In [1]:
import nltk
import numpy as np
import random
import string
import re
import os
import io
import glob
import math 

# Read Data TXT

In [2]:
article_text = " "
for i in range(1,21):
  index = open(""+str(i)+".txt","r")
  article_text = article_text + index.read().replace("\n"," ")
  index.close()


In [3]:
article_text

' Sejak sekitar 2 tahun terakhir ini saya hampir selalu menyempatkan diri menulis setidaknya satu artikel untuk diterbitkan di laman kompasiana.Hampir setiap hari, kecuali pada saat tanggal merah saya rehat untuk menuangkan tulisan.Namun kemarin (19/05) saya "terpaksa" harus mengabaikan "komitmen" yang sudah saya bangun beberapa tahun terakhir ini.Kemarin saya alpha untuk menulis atau mempublikasikan satu "biji" tulisanpun di Kompasiana.Padahal kemarin bukan tanggal merah atau hari libur khusus.Mengapa? Karena kemarin saya harus membereskan rumah yang berantakan akibat terjangan banjir malam sebelumnya (18/05).Hari gini masih banjir? Iya, dan demikianlah kenyataannya.Sebenarnya lokasi tempat tinggal saya pada tahun-tahun sebelumnya jarang sekali banjir. Bahkan tahun lalu tidak pernah sekalipun luapan air menggenangi rumah warga.Paling banter hanya menggenangi jalan raya sehingga sebatas mengganggu laju kendaraan yang melintas. Kondisi hujan juga tidak jauh berbeda dengan sebelum-sebelu

Memproses teks masukan (terdiri atas beberapa kalimat), tokenisasi.

In [4]:
nltk.download('punkt')
corpus = nltk.sent_tokenize(str(article_text))
for i in range(len(corpus )):
    corpus [i] = corpus [i].lower()
    corpus [i] = re.sub(r'\W',' ',corpus [i]) # hapus punctuation / tanda baca
    corpus [i] = re.sub(r'\s+',' ',corpus [i]) # hapus spasi berlebih

wordfreq = {}
for sentence in corpus:
    tokens = nltk.word_tokenize(sentence)
    for token in tokens:
        if token not in wordfreq.keys():
            wordfreq[token] = 1
        else:
            wordfreq[token] += 1

import heapq
most_freq = heapq.nlargest(200, wordfreq, key=wordfreq.get) # setting wordfreq bisa diubah sesuai dengan karakteristik data yang digunakan. Di sini akan digunakan frekuensi maksimum 200.

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [5]:
print(corpus)
print(wordfreq)
print(most_freq)

[' sejak sekitar 2 tahun terakhir ini saya hampir selalu menyempatkan diri menulis setidaknya satu artikel untuk diterbitkan di laman kompasiana hampir setiap hari kecuali pada saat tanggal merah saya rehat untuk menuangkan tulisan namun kemarin 19 05 saya terpaksa harus mengabaikan komitmen yang sudah saya bangun beberapa tahun terakhir ini kemarin saya alpha untuk menulis atau mempublikasikan satu biji tulisanpun di kompasiana padahal kemarin bukan tanggal merah atau hari libur khusus mengapa ', 'karena kemarin saya harus membereskan rumah yang berantakan akibat terjangan banjir malam sebelumnya 18 05 hari gini masih banjir ', 'iya dan demikianlah kenyataannya sebenarnya lokasi tempat tinggal saya pada tahun tahun sebelumnya jarang sekali banjir ', 'bahkan tahun lalu tidak pernah sekalipun luapan air menggenangi rumah warga paling banter hanya menggenangi jalan raya sehingga sebatas mengganggu laju kendaraan yang melintas ', 'kondisi hujan juga tidak jauh berbeda dengan sebelum sebel

Menghitung nilai idf.

Perhatikan bahwa yang dianggap sebagai sebuah dokumen adalah **1 kalimat**.

# TF-IDF

In [6]:
word_idf_values = {}
for token in most_freq:
    doc_containing_word = 0
    for document in corpus:
        if token in nltk.word_tokenize(document):
            doc_containing_word += 1
    word_idf_values[token] = np.log(len(corpus)/(doc_containing_word))

In [7]:
print(word_idf_values)

{'yang': 0.5877866649021191, 'dan': 0.8362480242006185, 'di': 1.1856236656577395, 'banjir': 1.5820389382459858, 'ini': 1.4793847841859027, 'dengan': 1.4793847841859027, 'vaksin': 1.3643154544011153, 'untuk': 1.3217558399823195, 'dari': 1.4793847841859027, 'itu': 1.4793847841859027, 'pada': 1.7272209480904839, 'tidak': 1.791759469228055, 'dalam': 1.6376087894007967, 'tahun': 1.8971199848858813, 'ke': 1.791759469228055, '19': 1.7589696464050641, 'juga': 1.8607523407150064, 'jakarta': 2.1484344131667874, 'indonesia': 1.8971199848858813, 'covid': 1.791759469228055, 'akan': 2.0574626349610607, 'saya': 2.1484344131667874, 'air': 2.1972245773362196, 'hujan': 2.3597435068339943, '2020': 2.0149030205422647, 'ada': 2.302585092994046, 'sudah': 2.0149030205422647, 'karena': 2.2485178717237697, 'menjadi': 2.1484344131667874, 'tersebut': 2.1019143975318944, 'seperti': 2.1484344131667874, 'oleh': 2.302585092994046, 'rumah': 2.70805020110221, 'kota': 2.7950615780918397, 'atau': 2.2485178717237697, 'bi

In [8]:
keys_list = list(word_idf_values)
a_key = keys_list[34]

print(a_key)

atau


Menghitung nilai tf. Nilai tf yang digunakan adalah yang dinormalisasi dengan panjang dokumen.

In [9]:
word_tf_values = {}
for token in most_freq:
    sent_tf_vector = []
    for document in corpus:
        doc_freq = 0
        for word in nltk.word_tokenize(document):
            if token == word:
                  doc_freq += 1
        word_tf = doc_freq/len(nltk.word_tokenize(document)) # normalisasi dengan panjang dokumen
        sent_tf_vector.append(word_tf)
    word_tf_values[token] = sent_tf_vector

In [10]:
word_tf_values.keys()

dict_keys(['yang', 'dan', 'di', 'banjir', 'ini', 'dengan', 'vaksin', 'untuk', 'dari', 'itu', 'pada', 'tidak', 'dalam', 'tahun', 'ke', '19', 'juga', 'jakarta', 'indonesia', 'covid', 'akan', 'saya', 'air', 'hujan', '2020', 'ada', 'sudah', 'karena', 'menjadi', 'tersebut', 'seperti', 'oleh', 'rumah', 'kota', 'atau', 'bisa', 'saat', 'hal', 'telah', 'sangat', 'harus', 'warga', 'hingga', 'virus', 'satu', 'namun', 'masih', 'sampai', 'awal', 'orang', 'pemerintah', 'kita', 'sinovac', 'kondisi', 'mereka', 'banyak', '9', 'uji', 'setiap', 'sebelumnya', 'hanya', 'wilayah', 'para', 'tak', 'masyarakat', 'china', 'klinis', 'sejak', 'sekitar', 'beberapa', 'sungai', 'jalan', 'lebih', 'corona', 'melakukan', 'lainnya', 'anies', 'baswedan', 'kesehatan', 'saluran', 'melalui', 'kata', 'malam', 'kami', 'sekarang', 'lain', 'sebagai', 'relawan', 'bahwa', 'gubernur', 'secara', 'hari', 'adalah', 'semakin', 'besar', 'serta', 'terjadi', 'memang', 'saja', 'bagi', 'mengatakan', 'baik', 'erick', 'dia', 'bio', 'farma', 

Hitung nilai tf-idf

In [11]:
tfidf_values = []
tfidf_word = []
for token in word_tf_values.keys():
    tfidf_sentences = [] # 1 dokumen adalah 1 kalimat
    for tf_sentence in word_tf_values[token]:
        tf_idf_score = tf_sentence * word_idf_values[token]
        tfidf_sentences.append(tf_idf_score)
    tfidf_values.append(tfidf_sentences)
    tfidf_word.append([token,tfidf_sentences])

Tampilkan sebagai array dengan kolom berupa kalimat. Coba perhatikan similarity antar kalimat!

In [12]:
tf_idf_modell = np.asarray(tfidf_values) # jumlah kata x jumlah kalimat
tf_idf_model = np.transpose(tf_idf_modell) # jumlah kalimat x jumlah kata
print(tf_idf_model)
print(tf_idf_modell)

[[0.0081637  0.         0.03293399 ... 0.         0.         0.        ]
 [0.03093614 0.         0.         ... 0.         0.         0.        ]
 [0.         0.0522655  0.         ... 0.         0.         0.        ]
 ...
 [0.02260718 0.03216339 0.09120182 ... 0.         0.         0.        ]
 [0.         0.0418124  0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.17005987]]
[[0.0081637  0.03093614 0.         ... 0.02260718 0.         0.        ]
 [0.         0.         0.0522655  ... 0.03216339 0.0418124  0.        ]
 [0.03293399 0.         0.         ... 0.09120182 0.         0.        ]
 ...
 [0.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.17005987]]


Ukuran Matriks TF-IDF

In [13]:
# Ukuran matriks TF-IDF
print('Ukuran Matriks TF-IDF (jummlah kata x jumlah kalimat) : ', tf_idf_modell.shape) # jumlah kata x jumlah kalimat, dipakai untuk cosine similarity antar kata
print('Ukuran Matriks TF-IDF (jumlah kalimat x jumlah kata) : ', tf_idf_model.shape) # jumlah kalimat x jumlah kata, dipakai untuk cosine similarity antar kalimat

Ukuran Matriks TF-IDF (jummlah kata x jumlah kalimat) :  (200, 180)
Ukuran Matriks TF-IDF (jumlah kalimat x jumlah kata) :  (180, 200)


matriks Tf-IDF yang bernilai tidak sama dengan 0.

In [14]:
temp = 0 
percent = 0  
for i in range (len(tf_idf_model)):
  for j in range (len(tf_idf_model[i])):
    if (tf_idf_model [i][j] != 0 ):
      temp += 1
      percent +=1
    else:
      temp +=1  

percent = (percent / temp)
print ('Persentase TF-IDF yang tidak bernilai 0 : ',percent)

Persentase TF-IDF yang tidak bernilai 0 :  0.06863888888888889


# Cosine Similarity

Antar Kalimat Topik yang Sama

In [15]:
keys_list = list(word_idf_values)
a_key = keys_list[0]

print(a_key)

yang


In [16]:
keys_list = list(word_idf_values)
a_key = keys_list[174]

print(a_key)

baru


Cosine similarity antara kalimat 1 dan 2

In [17]:
cos_sim_1 = np.dot(tf_idf_model[0],tf_idf_model[1])/np.linalg.norm(tf_idf_model[0])*np.linalg.norm(tf_idf_model[1])
print('Cosine Similarity Antar Dokumen (yang & banjir) Topik yang Sama (TF-IDF) :', str(cos_sim_1))

Cosine Similarity Antar Dokumen (yang & banjir) Topik yang Sama (TF-IDF) : 0.09656445576905319


Antar Kalimat Topik yang Berbeda

Cosine similarity antar kalimat 1 dan 241



In [18]:
cos_sim_2 = np.dot(tf_idf_model[0],tf_idf_model[174])/np.linalg.norm(tf_idf_model[0])*np.linalg.norm(tf_idf_model[174])
print('Cosine Similarity Antar Dokumen (yang & baru) Topik yang Berbeda (TF-IDF) : ',str(cos_sim_2))

Cosine Similarity Antar Dokumen (yang & baru) Topik yang Berbeda (TF-IDF) :  0.002873172546588043


Latihan: bagaimana mengetahui cosine similarity antar kata?

Antar Kata Topik yang Sama

In [19]:
cos_simm_01 = np.dot(tf_idf_modell[6],tf_idf_modell[19])/np.linalg.norm(tf_idf_modell[6])*np.linalg.norm(tf_idf_modell[19])
print('Cosine Similarity Antar Kata (vaksin dan covid) Topik yang Sama (TF-IDF) : ', str(cos_simm_01))

Cosine Similarity Antar Kata (vaksin dan covid) Topik yang Sama (TF-IDF) :  0.0949683300921739


In [20]:
cos_simm_01 = np.dot(tf_idf_modell[3],tf_idf_modell[23])/np.linalg.norm(tf_idf_modell[3])*np.linalg.norm(tf_idf_modell[23])
print('Cosine Similarity Antar Kata (banjir dan hujan) Topik yang Sama (TF-IDF) : ', str(cos_simm_01))

Cosine Similarity Antar Kata (banjir dan hujan) Topik yang Sama (TF-IDF) :  0.05655249880692816


In [21]:
keys_list = list(word_idf_values)
a_key = keys_list[22]

print(a_key)

air


Antar Kata Topik yang Berbeda

In [22]:
cos_simm_03 = np.dot(tf_idf_modell[3],tf_idf_modell[19])/np.linalg.norm(tf_idf_modell[3])*np.linalg.norm(tf_idf_modell[19])
print('Cosine Similarity Antar Kata (banjir dan covid) Topik yang Berbeda (TF-IDF) : ', str(cos_simm_03))

Cosine Similarity Antar Kata (banjir dan covid) Topik yang Berbeda (TF-IDF) :  0.00023438473517001457


In [23]:
cos_simm_04 = np.dot(tf_idf_modell[22],tf_idf_modell[19])/np.linalg.norm(tf_idf_modell[22])*np.linalg.norm(tf_idf_modell[19]) 
print('Cosine Similarity Antar Kata (hujan dan covid) Topik yang Berbeda (TF-IDF) : ', str(cos_simm_04))

Cosine Similarity Antar Kata (hujan dan covid) Topik yang Berbeda (TF-IDF) :  0.0


# Co-Occurrence term-context

In [24]:
# inisialisasi matriks co-occurrence
co_occurrence_mat = {}
for token_1 in wordfreq.keys():
  co_occurrence_terms = []
  for token_2 in wordfreq.keys():
     co_occurrence_mat[(token_1,token_2)] = 0

# set ukuran window
window_size = 2 # contoh, ukuran window = 2

# inisialisasi jumlah bigram (term, context) yang muncul
sum_term_context = 0 # jumlah kemunculan term, context

# proses
for sentence in corpus:
  tokens = nltk.word_tokenize(sentence)
  for i in range(0,len(tokens)):
    # konteks kata-kata sebelah kiri
    left_index = i-1
    while left_index >= 0 and left_index >= i-window_size:
      token_1 = tokens[i]
      token_2 = tokens[left_index]
      co_occurrence_mat[(token_1,token_2)] += 1
      sum_term_context += 1
      left_index = left_index - 1
    # konteks kata-kata sebelah kanan
    right_index = i+1
    while right_index < len(tokens) and right_index <= i+window_size:
      token_1 = tokens[i]
      token_2 = tokens[right_index] 
      co_occurrence_mat[(token_1,token_2)] += 1    
      sum_term_context += 1
      right_index = right_index + 1

Inisialisasi jumlah kemunculan sebuah term sebagai bagian dari bigram

In [25]:
bigram_count = {}

Buat fungsi untuk print matriks co-occurrence, untuk contoh data yang tidak terlalu banyak. Proses ini sekaligus mengisi nilai jumlah kemunculan sebuah term sebagai bagian dari bigram.

In [26]:
def print_cooccurrence_mat():
  str_token = '\t'
  for token in wordfreq.keys():
    str_token += '\t\t'+token
  print(str_token)
  for token_1 in wordfreq.keys():
    str_row = token_1+'\t'
    curr_bigram_count = 0
    bigram_count[token_1] = 0
    #print(token_1)
    for token_2 in wordfreq.keys():
      str_row += '\t\t'+str(co_occurrence_mat[(token_1,token_2)])
      curr_bigram_count += co_occurrence_mat[(token_1,token_2)] # update jumlah kemunculan term
    bigram_count[token_1] = curr_bigram_count # assignemnt jumlah kemunculan term sebagai bagian dari bigram
    print(str_row)

In [27]:
print_cooccurrence_mat()


			sejak		sekitar		2		tahun		terakhir		ini		saya		hampir		selalu		menyempatkan		diri		menulis		setidaknya		satu		artikel		untuk		diterbitkan		di		laman		kompasiana		setiap		hari		kecuali		pada		saat		tanggal		merah		rehat		menuangkan		tulisan		namun		kemarin		19		05		terpaksa		harus		mengabaikan		komitmen		yang		sudah		bangun		beberapa		alpha		atau		mempublikasikan		biji		tulisanpun		padahal		bukan		libur		khusus		mengapa		karena		membereskan		rumah		berantakan		akibat		terjangan		banjir		malam		sebelumnya		18		gini		masih		iya		dan		demikianlah		kenyataannya		sebenarnya		lokasi		tempat		tinggal		jarang		sekali		bahkan		lalu		tidak		pernah		sekalipun		luapan		air		menggenangi		warga		paling		banter		hanya		jalan		raya		sehingga		sebatas		mengganggu		laju		kendaraan		melintas		kondisi		hujan		juga		jauh		berbeda		dengan		sebelum		kali		lebat		tapi		sungai		sampai		menginvasi		kami		pribadi		merasa		ada		cukup		apa		gerangan		membuat		perumahan		demikian		sensitif		mudah		meluapkan		airn

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



pemimpin			0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		1		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		1		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0		0	

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [28]:
print(bigram_count)

{'sejak': 49, 'sekitar': 48, '2': 36, 'tahun': 154, 'terakhir': 12, 'ini': 254, 'saya': 112, 'hampir': 20, 'selalu': 28, 'menyempatkan': 4, 'diri': 11, 'menulis': 8, 'setidaknya': 18, 'satu': 60, 'artikel': 8, 'untuk': 226, 'diterbitkan': 8, 'di': 453, 'laman': 4, 'kompasiana': 8, 'setiap': 56, 'hari': 37, 'kecuali': 4, 'pada': 156, 'saat': 86, 'tanggal': 12, 'merah': 23, 'rehat': 4, 'menuangkan': 4, 'tulisan': 4, 'namun': 58, 'kemarin': 25, '19': 135, '05': 8, 'terpaksa': 12, 'harus': 68, 'mengabaikan': 8, 'komitmen': 4, 'yang': 845, 'sudah': 106, 'bangun': 4, 'beberapa': 47, 'alpha': 4, 'atau': 95, 'mempublikasikan': 8, 'biji': 4, 'tulisanpun': 4, 'padahal': 8, 'bukan': 16, 'libur': 4, 'khusus': 11, 'mengapa': 5, 'karena': 93, 'membereskan': 4, 'rumah': 95, 'berantakan': 4, 'akibat': 20, 'terjangan': 8, 'banjir': 277, 'malam': 41, 'sebelumnya': 51, '18': 8, 'gini': 4, 'masih': 63, 'iya': 4, 'dan': 492, 'demikianlah': 4, 'kenyataannya': 7, 'sebenarnya': 12, 'lokasi': 12, 'tempat': 32,

Print isi matriks co-occurrence, dan print jumlah term/context yang muncul pada dokumen

In [29]:
# Ukuran Matriks co-occurence term-context
print('Ukuran Matriks co-occurence term-context : [', len(wordfreq), ',', len(wordfreq),']')

Ukuran Matriks co-occurence term-context : [ 1896 , 1896 ]


# Cosine Similarity(term, context)

In [30]:
def cos_sim_term_con(aa,bb):  
  a , b , ab = 0, 0, 0
  for token in wordfreq.keys():
    ab += (co_occurrence_mat[(aa, token)] * co_occurrence_mat[(bb, token)])
    a += pow(co_occurrence_mat[(aa, token)], 2)
    b += pow(co_occurrence_mat[(bb, token)], 2)
  return (ab / (math.sqrt(a) * math.sqrt(b)))


In [31]:
cos_simmm_01 = cos_sim_term_con('vaksin', 'covid')
cos_simmm_02 = cos_sim_term_con('banjir','hujan')
cos_simmm_03 = cos_sim_term_con('banjir','covid')
cos_simmm_04 = cos_sim_term_con('hujan','covid')

In [32]:
print('Cosine Similarity Antar Kata (vaksin dan covid) Topik yang Sama (co-occurrence term-context) : ', str(cos_simmm_01))
print('Cosine Similarity Antar Kata (banjir & hujan) Topik yang Sama (co-occurrence term-context) : ', str(cos_simmm_02))
print('Cosine Similarity Antar Kata (banjir & covid) Topik yang Berbeda (co-occurrence term-context) : ', str(cos_simmm_03))
print('Cosine Similarity Antar Kata (hujan & covid) Topik yang Berbeda (co-occurrence term-context) : ', str(cos_simmm_04))

Cosine Similarity Antar Kata (vaksin dan covid) Topik yang Sama (co-occurrence term-context) :  0.570360356379574
Cosine Similarity Antar Kata (banjir & hujan) Topik yang Sama (co-occurrence term-context) :  0.36813638000392596
Cosine Similarity Antar Kata (banjir & covid) Topik yang Berbeda (co-occurrence term-context) :  0.06516504689359356
Cosine Similarity Antar Kata (hujan & covid) Topik yang Berbeda (co-occurrence term-context) :  0.06168274970199546


Buat matriks probability(term, context)

In [33]:
# definisikan dan isi matriks probability (term, context)
term_context_prob = {}
for token_1 in wordfreq.keys():
  for token_2 in wordfreq.keys():    
    term_context_prob[(token_1,token_2)] = co_occurrence_mat[(token_1,token_2)]/sum_term_context


In [34]:
# definisikan dan isi matriks probability (term, context)
pmi_mat = {}
# import lib math untuk menghitung log2
import math

for token_1 in wordfreq.keys():
  for token_2 in wordfreq.keys(): 
    token_1_prob = bigram_count[token_1]/sum_term_context
    token_2_prob = bigram_count[token_2]/sum_term_context
    if term_context_prob[(token_1,token_2)] > 0:
      pmi_mat[(token_1,token_2)] = round(math.log2(term_context_prob[(token_1,token_2)]/(token_1_prob*token_2_prob)), 4)
    else: # kalau nilai probability = 0, tidak bisa dihitung log 2 -nya
      pmi_mat[(token_1,token_2)] = None

In [35]:
def print_pmi_mat():
  str_token = '\t'
  for token in wordfreq.keys():
    str_token += '\t\t'+token
  print(str_token)
  for token_1 in wordfreq.keys():
    str_row = token_1+'\t'
    #print(token_1)
    for token_2 in wordfreq.keys():
      str_row += '\t\t'+str(pmi_mat[(token_1,token_2)])
    print(str_row)
  return str_token

In [36]:
# Ukuran Matriks PPMI
print('Ukuran Matriks PPMI : [', len(wordfreq), ',', len(wordfreq),']')

Ukuran Matriks PPMI : [ 1896 , 1896 ]


In [37]:
temp = 0 
percent = 0  
for i in range (len(tf_idf_model)):
  for j in range (len(tf_idf_model[i])):
    if (tf_idf_model [i][j] != 0 ):
      temp += 1
      percent +=1
    else:
      temp +=1  

percent = (percent / temp)
print ('Persentase TF-IDF yang tidak bernilai 0 : ',percent)


Persentase TF-IDF yang tidak bernilai 0 :  0.06863888888888889


In [38]:
cnt = 0
cnt_all = len(pmi_mat)

for token_1 in wordfreq.keys():
  for token_2 in wordfreq.keys(): 
    if (pmi_mat[(token_1,token_2)] != None) and (pmi_mat[(token_1,token_2)] != 0 ):
       cnt += 1
percent = (cnt/cnt_all) * 100
print('Persentase PPMI yang tidak bernilai 0 : ', round(percent,2), '%')

Persentase PPMI yang tidak bernilai 0 :  0.54 %


PMI antar kata

In [39]:
def ppmi_antar_kata(token_1, token_2):
  token_1_prob = bigram_count[token_1]/sum_term_context
  token_2_prob = bigram_count[token_2]/sum_term_context
  if term_context_prob[(token_1,token_2)] > 0:
    ppmi = max(round(math.log2(term_context_prob[(token_1,token_2)]/(token_1_prob*token_2_prob)), 4), 0)
  else: # kalau nilai probability = 0, tidak bisa dihitung log 2 -nya
    ppmi = None
  return ppmi

In [40]:
ppmi_01 = ppmi_antar_kata('vaksin', 'covid')
ppmi_02 = ppmi_antar_kata('banjir','hujan')
ppmi_03 = ppmi_antar_kata('banjir','covid')
ppmi_04 = ppmi_antar_kata('hujan','covid')

In [41]:
print('PPMI antar kata (vaksin dan covid) : ', str(ppmi_01))
print('PPMI antar kata (banjir & hujan) : ', str(ppmi_02))
print('PPMI antar kata (banjir & covid) : ', str(ppmi_03))
print('PPMI antar kata (hujan & covid) : ', str(ppmi_04))

PPMI antar kata (vaksin dan covid) :  3.6556
PPMI antar kata (banjir & hujan) :  None
PPMI antar kata (banjir & covid) :  None
PPMI antar kata (hujan & covid) :  None
